## System Setup

In [ ]:
# Find CPU info
!grep -m1 'model name' /proc/cpuinfo | awk -F": " '{print $2}'
!grep 'cpu cores' /proc/cpuinfo | awk -F": " '{a[cores]+=$2}END{print "CPU cores: " a[cores]}'

Intel(R) Xeon(R) CPU @ 2.20GHz
CPU cores: 8


In [ ]:
# Find Ram Info
!grep MemTotal /proc/meminfo | awk '{printf "%.1fGB RAM", $2 / 1024 / 1024}'

25.5GB RAM

In [ ]:
!python3 --version

Python 3.10.6


In [ ]:
!nvidia-smi

Sun Jul 23 16:46:56 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.105.17   Driver Version: 525.105.17   CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   34C    P0    23W / 300W |      0MiB / 16384MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
!pip install pyBKTR

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 220.3/220.3 kB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.9/88.9 kB 5.0 MB/s eta 0:00:00


## Imputation Analysis (Python)

In [ ]:
from pyBKTR.bktr import BKTRRegressor
from pyBKTR.kernels import KernelMatern, KernelParameter,KernelSE
from pyBKTR.tensor_ops import TSR

import numpy as np
import pandas as pd

from pyBKTR.utils import simulate_spatiotemporal_data

df_res_arr = []
TSR.set_params('float32', 'cuda', 2)

for len_scale in [3, 6]:
    for miss_perc in [0.1, 0.5, 0.9]:
        for i in range(1, 11):
            spatial_kernel = KernelMatern(
                smoothness_factor = 5,
                lengthscale = KernelParameter(value = len_scale)
            )
            temporal_kernel = KernelSE(
                lengthscale = KernelParameter(value = len_scale)
            )

            simu_data = simulate_spatiotemporal_data(
                nb_locations=100,
                nb_time_points=150,
                nb_spatial_dimensions=2,
                spatial_scale=10,
                time_scale=10,
                spatial_covariates_means=[0, 2, 4],
                temporal_covariates_means=[1, 3],
                spatial_kernel=spatial_kernel,
                temporal_kernel=temporal_kernel,
                noise_variance_scale=1
            )

            data_df = simu_data['data_df'].copy()
            spatial_positions_df = simu_data['spatial_positions_df']
            temporal_positions_df = simu_data['temporal_positions_df']
            index_choices_tsr = TSR.tensor(list(range(len(data_df))))
            nb_miss_index = round(miss_perc * len(data_df))
            na_index = TSR.rand_choice(
                index_choices_tsr, nb_miss_index, use_replace=False
            ).cpu().numpy().astype(int)
            data_df.iloc[na_index, 0] = pd.NA

            bktr_regressor = BKTRRegressor(
                data_df = data_df,
                rank_decomp = 10,
                burn_in_iter = 500,
                sampling_iter = 500,
                spatial_kernel = KernelMatern(smoothness_factor = 5),
                spatial_positions_df = simu_data['spatial_positions_df'],
                temporal_kernel = KernelSE(),
                temporal_positions_df = simu_data['temporal_positions_df'],
                has_geo_coords = False
            )
            bktr_regressor.mcmc_sampling()

            y_err = bktr_regressor.imputed_y_estimates.iloc[na_index][['y']].to_numpy() - simu_data['data_df'].iloc[na_index][['y']].to_numpy()
            beta_err = np.abs(bktr_regressor.beta_estimates.to_numpy() - simu_data['beta_df'].to_numpy())
            y_rmse = float(np.sqrt(np.mean(y_err**2)))
            y_mae = float(np.mean(abs(y_err)))
            beta_rmse = float(np.sqrt(np.mean(beta_err**2)))
            beta_mae = float(np.mean(abs(beta_err)))

            df_res_arr.append([
                len_scale,
                miss_perc,
                i,
                beta_mae,
                beta_rmse,
                y_mae,
                y_rmse,
                bktr_regressor.result_logger.total_elapsed_time
            ])
            df = pd.DataFrame(df_res_arr, columns=['Lengthscale', 'Missing', 'Iter', 'B_MAE', 'B_RMSE', 'Y_MAE', 'Y_RMSE', 'Time'])
            print(df)



/usr/local/lib/python3.10/dist-packages/torch/distributions/wishart.py:253: UserWarning: Singular sample detected.
  warnings.warn("Singular sample detected.")


* Iter 1     | Elapsed     0.04s | MAE  7.1127 | RMSE  9.3642 *
* Iter 2     | Elapsed     0.04s | MAE  2.4696 | RMSE  3.1776 *
* Iter 3     | Elapsed     0.04s | MAE  1.4995 | RMSE  1.9533 *
* Iter 4     | Elapsed     0.05s | MAE  1.1885 | RMSE  1.5274 *
* Iter 5     | Elapsed     0.07s | MAE  1.0431 | RMSE  1.3264 *
* Iter 6     | Elapsed     0.05s | MAE  0.9425 | RMSE  1.1898 *
* Iter 7     | Elapsed     0.09s | MAE  0.9198 | RMSE  1.1649 *
* Iter 8     | Elapsed     0.08s | MAE  0.9130 | RMSE  1.1496 *
* Iter 9     | Elapsed     0.10s | MAE  0.9100 | RMSE  1.1438 *
* Iter 10    | Elapsed     0.06s | MAE  0.9027 | RMSE  1.1367 *
* Iter 11    | Elapsed     0.06s | MAE  0.8982 | RMSE  1.1319 *
* Iter 12    | Elapsed     0.08s | MAE  0.8938 | RMSE  1.1255 *
* Iter 13    | Elapsed     0.07s | MAE  0.8927 | RMSE  1.1242 *
* Iter 14    | Elapsed     0.08s | MAE  0.8910 | RMSE  1.1242 *
* Iter 15    | Elapsed     0.06s | MAE  0.8904 | RMSE  1.1201 *
* Iter 16    | Elapsed     0.07s | MAE  

/usr/local/lib/python3.10/dist-packages/torch/distributions/wishart.py:253: UserWarning: Singular sample detected.
  warnings.warn("Singular sample detected.")


* Iter 1     | Elapsed     0.04s | MAE  2.8381 | RMSE  3.7031 *
* Iter 2     | Elapsed     0.06s | MAE  1.6624 | RMSE  2.2098 *
* Iter 3     | Elapsed     0.03s | MAE  1.2185 | RMSE  1.5864 *
* Iter 4     | Elapsed     0.05s | MAE  1.0584 | RMSE  1.3604 *
* Iter 5     | Elapsed     0.05s | MAE  1.0074 | RMSE  1.2864 *
* Iter 6     | Elapsed     0.07s | MAE  0.9901 | RMSE  1.2639 *
* Iter 7     | Elapsed     0.08s | MAE  0.9830 | RMSE  1.2514 *
* Iter 8     | Elapsed     0.10s | MAE  0.9735 | RMSE  1.2404 *
* Iter 9     | Elapsed     0.06s | MAE  0.9673 | RMSE  1.2334 *
* Iter 10    | Elapsed     0.08s | MAE  0.9667 | RMSE  1.2284 *
* Iter 11    | Elapsed     0.10s | MAE  0.9623 | RMSE  1.2262 *
* Iter 12    | Elapsed     0.08s | MAE  0.9574 | RMSE  1.2193 *
* Iter 13    | Elapsed     0.08s | MAE  0.9538 | RMSE  1.2140 *
* Iter 14    | Elapsed     0.09s | MAE  0.9487 | RMSE  1.2061 *
* Iter 15    | Elapsed     0.05s | MAE  0.9440 | RMSE  1.1986 *
* Iter 16    | Elapsed     0.09s | MAE  

/usr/local/lib/python3.10/dist-packages/torch/distributions/wishart.py:253: UserWarning: Singular sample detected.
  warnings.warn("Singular sample detected.")


...

* Iter 2     | Elapsed     0.05s | MAE  1.9822 | RMSE  2.5968 *
* Iter 3     | Elapsed     0.05s | MAE  1.1050 | RMSE  1.4013 *
* Iter 4     | Elapsed     0.05s | MAE  0.8969 | RMSE  1.1194 *
* Iter 5     | Elapsed     0.07s | MAE  0.8517 | RMSE  1.0672 *
* Iter 6     | Elapsed     0.11s | MAE  0.8396 | RMSE  1.0507 *
* Iter 7     | Elapsed     0.04s | MAE  0.8165 | RMSE  1.0240 *
* Iter 8     | Elapsed     0.06s | MAE  0.8201 | RMSE  1.0258 *
* Iter 9     | Elapsed     0.10s | MAE  0.8120 | RMSE  1.0154 *
* Iter 10    | Elapsed     0.07s | MAE  0.8165 | RMSE  1.0205 *
* Iter 11    | Elapsed     0.05s | MAE  0.8280 | RMSE  1.0332 *
* Iter 12    | Elapsed     0.07s | MAE  0.8172 | RMSE  1.0162 *
* Iter 13    | Elapsed     0.05s | MAE  0.8190 | RMSE  1.0231 *
* Iter 14    | Elapsed     0.10s | MAE  0.8121 | RMSE  1.0219 *
* Iter 15    | Elapsed     0.05s | MAE  0.8161 | RMSE  1.0235 *
* Iter 16    | Elapsed     0.05s | MAE  0.8109 | RMSE  1.0149 *
* Iter 17    | Elapsed     0.09s | MAE  

/usr/local/lib/python3.10/dist-packages/torch/distributions/wishart.py:253: UserWarning: Singular sample detected.
  warnings.warn("Singular sample detected.")


* Iter 1     | Elapsed     0.05s | MAE  7.4033 | RMSE  9.5090 *
* Iter 2     | Elapsed     0.04s | MAE  3.2584 | RMSE  4.2571 *
* Iter 3     | Elapsed     0.07s | MAE  1.4478 | RMSE  1.8759 *
* Iter 4     | Elapsed     0.05s | MAE  1.0358 | RMSE  1.3033 *
* Iter 5     | Elapsed     0.08s | MAE  0.9075 | RMSE  1.1233 *
* Iter 6     | Elapsed     0.04s | MAE  0.8602 | RMSE  1.0600 *
* Iter 7     | Elapsed     0.05s | MAE  0.8417 | RMSE  1.0527 *
* Iter 8     | Elapsed     0.06s | MAE  0.8545 | RMSE  1.0629 *
* Iter 9     | Elapsed     0.09s | MAE  0.8501 | RMSE  1.0661 *
* Iter 10    | Elapsed     0.06s | MAE  0.8440 | RMSE  1.0562 *
* Iter 11    | Elapsed     0.10s | MAE  0.8300 | RMSE  1.0395 *
* Iter 12    | Elapsed     0.07s | MAE  0.8418 | RMSE  1.0463 *
* Iter 13    | Elapsed     0.08s | MAE  0.8400 | RMSE  1.0472 *
* Iter 14    | Elapsed     0.09s | MAE  0.8293 | RMSE  1.0332 *
* Iter 15    | Elapsed     0.06s | MAE  0.8403 | RMSE  1.0483 *
* Iter 16    | Elapsed     0.06s | MAE  

/usr/local/lib/python3.10/dist-packages/torch/distributions/wishart.py:253: UserWarning: Singular sample detected.
  warnings.warn("Singular sample detected.")


* Iter 2     | Elapsed     0.04s | MAE  2.2052 | RMSE  2.9893 *
* Iter 3     | Elapsed     0.04s | MAE  1.1371 | RMSE  1.5061 *
* Iter 4     | Elapsed     0.06s | MAE  0.8627 | RMSE  1.1059 *
* Iter 5     | Elapsed     0.06s | MAE  0.7993 | RMSE  1.0131 *
* Iter 6     | Elapsed     0.05s | MAE  0.7829 | RMSE  0.9950 *
* Iter 7     | Elapsed     0.05s | MAE  0.8105 | RMSE  1.0171 *
* Iter 8     | Elapsed     0.05s | MAE  0.7943 | RMSE  1.0128 *
* Iter 9     | Elapsed     0.06s | MAE  0.7957 | RMSE  1.0161 *
* Iter 10    | Elapsed     0.08s | MAE  0.8006 | RMSE  1.0156 *
* Iter 11    | Elapsed     0.07s | MAE  0.7939 | RMSE  1.0107 *
* Iter 12    | Elapsed     0.07s | MAE  0.7879 | RMSE  1.0048 *
* Iter 13    | Elapsed     0.06s | MAE  0.7766 | RMSE  0.9877 *
* Iter 14    | Elapsed     0.08s | MAE  0.7845 | RMSE  0.9930 *
* Iter 15    | Elapsed     0.07s | MAE  0.7768 | RMSE  0.9907 *
* Iter 16    | Elapsed     0.07s | MAE  0.7789 | RMSE  0.9958 *
* Iter 17    | Elapsed     0.03s | MAE  